# Cars: Getting Started

In [2]:
import numpy as np 
import pandas as pd 
import seaborn as sns 
import pyblp
sns.set_theme()
import matplotlib.pyplot as plt

pyblp.options.digits = 2
pyblp.options.verbose = False

# Read in data

The dataset, `cars.csv`, contains cleaned and processed data. If you want to make changes, the notebook, `materialize.ipynb`, creates the data from the raw source datsets. 

In [3]:
cars = pd.read_csv('cars.csv') # this reads the *balanced* dataset (i.e. J = 40 products per market always)
# cars = pd.read_excel('cars.xlsx') # this reads the *unbalanced* dataset (i.e. J varies over time)

### No data for France pre 1990. Average growth in adult fraction from other countries applied each year before

In [4]:
AdultFrac = pd.read_excel("FracOver20.xlsx", index_col = 0)
cars['adults'] = None
for idx in cars.index:
    cars['adults'][idx] = AdultFrac[cars['ma'][idx]][cars['ye'][idx]]

/var/folders/qr/xw8cgrnd4098yvfl09hlrdl80000gn/T/ipykernel_45304/553329577.py:4: FutureWarning: ChainedAssignmentError: behaviour will change in pandas 3.0!
You are setting values through chained assignment. Currently this works in certain cases, but when using Copy-on-Write (which will become the default behaviour in pandas 3.0) this will never work to update the original DataFrame or Series, because the intermediate object on which we are setting values will behave as a copy.
A typical example is when you are setting values in a column of a DataFrame, like:

df["col"][row_indexer] = value

Use `df.loc[row_indexer, "col"] = values` instead, to perform the assignment in a single step and ensure this keeps updating the original `df`.

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

  cars['adults'][idx] = AdultFrac[cars['ma'][idx]][cars['ye'][idx]]
/var/folders/qr/xw8cgrnd4098yvfl09hlrdl80000gn/T

We estimate that 77% of the adult population have a driving license for a full-car. Hence, the share of population aged 20+ with a driver becomes:

In [5]:
license_share = 0.77
cars["ad_w_li"] = cars["adults"] * license_share 

In [6]:
lbl_vars = pd.read_csv('labels_variables.csv', index_col=0)
lbl_vals = pd.read_stata('cars.dta', iterator=True).value_labels() # the values that variables take (not relevant for all )

## Overview of the dataset

In [7]:
pd.set_option('display.max_colwidth', None)
tab = cars.mean(numeric_only=True).apply(lambda x: f'{x:.2f}').to_frame('Mean').join(lbl_vars)
tab

Mean  \
ye                   84.50   
ma                    3.00   
co                  207.50   
zcode               177.76   
brd                  16.79   
org                   2.72   
loc                   5.17   
cla                   2.30   
home                  0.32   
frm                  14.50   
qu                35606.68   
cy                 1337.09   
hp                   50.10   
we                  934.49   
pl                    4.88   
do                    3.55   
le                  409.24   
wi                  163.44   
he                  140.46   
li1                   6.59   
li2                   8.11   
li3                   8.92   
li                    7.87   
sp                  154.22   
ac                   16.27   
pr              2608988.58   
princ                 0.76   
eurpr              7256.92   
exppr            600384.65   
avexr               229.30   
avdexr              319.91   
avcpr               492.53   
avppr               671.77   
avdcpr               77.02   
avdppr               87.69   
xexr                 66.32   
tax                   0.21   
pop            49183800.00   
ngdp    178667304825541.97   
rgdp    216716720230172.44   
engdp      504371708122.45   
ergdp      659002565347.56   
engdpc            10015.84   
ergdpc            13264.84   
inc               26829.74   

                                                                                   label  
ye                                                      year (=first dimension of panel)  
ma                                                   market (=second dimension of panel)  
co                                                model code (=third dimension of panel)  
zcode               alternative model code (predecessors and successors get same number)  
brd                                                                           brand code  
org              origin code (demand side, country with which consumers associate model)  
loc                location code (production side, country where producer produce model)  
cla                                                                class or segment code  
home                          domestic car dummy (appropriate interaction of org and ma)  
frm                                                                            firm code  
qu                                               sales (number of new car registrations)  
cy                                               cylinder volume or displacement (in cc)  
hp                                                                    horsepower (in kW)  
we                                                                        weight (in kg)  
pl                                                places (number, not reliable variable)  
do                                                 doors (number, not reliable variable)  
le                                                                        length (in cm)  
wi                                                                         width (in cm)  
he                                                                        height (in cm)  
li1                             measure 1 for fuel efficiency (liter per km, at 90 km/h)  
li2                            measure 2 for fuel efficiency (liter per km, at 120 km/h)  
li3                          measure 3 for fuel efficiency (liter per km, at city speed)  
li                                             average of li1, li2, li3 (used in papers)  
sp                                                               maximum speed (km/hour)  
ac          time to acceleration (in seconds from 0 to 100 km/h, some from 0 to 96 km/h)  
pr                                      price (in destination currency including V.A.T.)  
princ   =pr/(ngdp/pop): price relative to per capita income (often used in demand model)  
eurpr   =pr/avdexr: price in common currency (in SDR times 1.2956 to interpret in Euros)  
ex

# Set up for analysis

## Price variables 

Can be either price (`pr`), price-to-income (`princ`), or log price (`logp`, created below).

In [8]:
price_var = 'eurpr'

In [9]:
cars['logp'] = np.log(cars[price_var])

## Market share

**Todo:** Decide how to measure the market size and thereby the market share. *Note:* Below is just an example that sets the market size = population / 3. 

In [10]:
# total quantity of cars sold in market-year (ma, ye)
cars['qu_tot'] = cars.groupby(['ma', 'ye'])['qu'].transform('sum')
cars['market_size'] = cars['pop'] * cars['ad_w_li']
cars['s'] = cars['qu'] / cars['market_size']

In [11]:
# compute the share of the outside good (will be useful for the demand inversion)
cars['s0'] = 1.0 - cars.groupby(['ma', 'ye'])['s'].transform('sum')
print(f'Outside share is from {cars.s0.min():.1%} to {cars.s0.max():.1%}')

Outside share is from 93.1% to 97.1%


In [12]:
cars.groupby(['ma'])['s'].describe().rename(index=lbl_vals['market']).style.format('{:.3f}')

## 1. Using canned software

In [13]:
from linearmodels.iv import IV2SLS

In [14]:
cars['delta'] = cars['s'] / cars['s0']
cars['delta'] = np.log(cars['delta'].values.astype(float)) ## Den stoppede med at ville gøre det i et skridt uden at definere type

In [15]:
cars["brand"].replace('alfa romeo', 'alfa_romeo', inplace=True)
cars["brand"] = cars["brand"].str.replace('/', '', regex=False)

/var/folders/qr/xw8cgrnd4098yvfl09hlrdl80000gn/T/ipykernel_45304/3195240017.py:1: FutureWarning: A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values always behaves as a copy.

For example, when doing 'df[col].method(value, inplace=True)', try using 'df.method({col: value}, inplace=True)' or df[col] = df[col].method(value) instead, to perform the operation inplace on the original object.


  cars["brand"].replace('alfa romeo', 'alfa_romeo', inplace=True)


In [16]:
categorical_var = 'brand' # name of categorical variable
dummies = pd.get_dummies(cars[categorical_var]) # creates a matrix of dummies for each value of dummyvar
x_vars_dummies = list(dummies.columns[1:].values) # omit a reference category, here it is the first (hence columns[1:])

# add dummies to the dataframe 
assert dummies.columns[0] not in cars.columns, f'It looks like you have already added this dummy to the dataframe. Avoid duplicates! '
cars = pd.concat([cars,dummies], axis=1)

In [19]:
# Calculate the average price of all other cars in a given year in a given market:
# Step 1: Calculate the sum and count of prices for each year and market
cars['sum_eurpr_ye_ma'] = cars.groupby(['ye', 'ma'])['eurpr'].transform('sum')
cars['count_ye_ma'] = cars.groupby(['ye', 'ma'])['eurpr'].transform('count')

# Step 2: Calculate the average price excluding the current observation
cars['avg_eurpr_excl'] = (cars['sum_eurpr_ye_ma'] - cars['eurpr']) / (cars['count_ye_ma'] - 1)

# Drop the intermediate columns if they are no longer needed
cars.drop(columns=['sum_eurpr_ye_ma', 'count_ye_ma'], inplace=True)


cars['avg_eurpr_excl'] = np.log(cars['avg_eurpr_excl'])

In [20]:
# choose your preferred variables 
x_vars = ['logp', 'avg_eurpr_excl', 'home', 'cy', 'hp', 'we', 'li', 'sp'] + x_vars_dummies # <--- !!! CHOOSE HERE 
print(x_vars)

['logp', 'avg_eurpr_excl', 'home', 'cy', 'hp', 'we', 'li', 'sp', 'MCC', 'VW', 'alfa_romeo', 'audi', 'citroen', 'daewoo', 'daf', 'fiat', 'ford', 'honda', 'hyundai', 'innocenti', 'lancia', 'mazda', 'mercedes', 'mitsubishi', 'nissan', 'opel', 'peugeot', 'renault', 'rover', 'saab', 'seat', 'skoda', 'suzuki', 'talbot', 'talhillman', 'talmatra', 'talsimca', 'talsunb', 'toyota', 'volvo']


In [24]:
# set up the estimation equation
formula = 'delta ~ 1'
for x_ in x_vars:
    formula += ' + ' + x_
print(formula)

delta ~ 1 + logp + avg_eurpr_excl + home + cy + hp + we + li + sp + MCC + VW + alfa_romeo + audi + citroen + daewoo + daf + fiat + ford + honda + hyundai + innocenti + lancia + mazda + mercedes + mitsubishi + nissan + opel + peugeot + renault + rover + saab + seat + skoda + suzuki + talbot + talhillman + talmatra + talsimca + talsunb + toyota + volvo


In [25]:
# Estimate the model by OLS
OLSmodel = IV2SLS.from_formula(formula, cars).fit()
OLSmodel.summary

/opt/anaconda3/lib/python3.12/site-packages/linearmodels/iv/model.py:557: MissingValueWarning: 
Inputs contain missing values. Dropping rows with missing observations.
  super().__init__(


The Logit elasticities are 

$$
\mathcal{E}_{jk} \equiv \frac{\partial s_{jt}}{\partial p_{kt}} \frac{p_{kt}}{s_{jt}} = 
\begin{cases}
\alpha (\mathbf{1}\{j = k\} - s_{jt}) p_{kt} & \text{if price is in level},   \\
\alpha (\mathbf{1}\{j = k\} - s_{jt})        & \text{if price is in log }. 
\end{cases}
$$

In [23]:
beta = model.params
elast_own = beta['logp'] * (1 - cars['s'])
print(f'Price in logs:  Avg. own-price elasticity: {elast_own.mean(): .2%}')

elast_cross = - beta['logp'] * cars['s']
print(f'Price in logs:  Avg. cross-price elasticity: {elast_cross.mean(): .2%}')

Price in logs:  Avg. own-price elasticity: -47.17%
Price in logs:  Avg. cross-price elasticity:  0.06%


## IV-estimation

We use the 

In [22]:
K = len(x_vars)
N = cars.ma.nunique() * cars.ye.nunique()
J = 40 
x = cars[x_vars].values.reshape((N,J,K)).astype(float)
cars['outcome'] = cars['s'] / cars['s0']
y = cars['delta'].values.reshape((N,J))
# standardize x
x = ((x - x.mean(0).mean(0))/(x.std(0).std(0)))

# Towards non-linear estimation

In order to work with the logit model, you have to be able to compute the utility indices, which typically take the form of some inner product of an $x$-vector and a $\theta$ vector. This is illustrated for you below. Since `x` is `(N,J,K)` (i.e. `x[i,j,:]` gives the $K$-vector of regressors for the car `j` in market-period `i`), we just have to form the matrix product `x @ theta`, and Python will do the sum over the 3rd dimension of `x`. 

In [23]:
theta0 = np.zeros((K,))
v = x @ theta0 # how to multiply a trial value with the matrix of regressors 
np.exp(v) / np.sum(np.exp(v), 1, keepdims=True) # choice probabilities 

array([[nan, nan, nan, ..., nan, nan, nan],
       [nan, nan, nan, ..., nan, nan, nan],
       [nan, nan, nan, ..., nan, nan, nan],
       ...,
       [nan, nan, nan, ..., nan, nan, nan],
       [nan, nan, nan, ..., nan, nan, nan],
       [nan, nan, nan, ..., nan, nan, nan]])